In [1]:
import pm4py
import pandas as pd


In [2]:
event_log = pm4py.read_xes('/Users/liliiaaliakberova/Desktop/Study/TUe_3_semester/Advanced_PM/end_A_event_log.xes')

/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
parsing log, completed traces :: 100%|██| 17549/17549 [00:04<00:00, 3772.23it/s]


In [3]:
pm4py.get_end_activities(event_log)

{'A_Pending': 11804, 'A_Cancelled': 3382, 'A_Denied': 2363}

In [4]:
pm4py.get_start_activities(event_log)

{'A_Create Application': 17549}

In [5]:
# number of distinct trace variants
len(pm4py.get_variants_as_tuples(event_log))

28

In [6]:
df = pm4py.convert_to_dataframe(event_log)
df.head(5)

Action                EventID  EventOrigin org:resource   
0      Created  Application_652823628  Application       User_1  \
1  statechange   ApplState_1582051990  Application       User_1   
2  statechange    ApplState_642383566  Application       User_1   
3  statechange     ApplState_99568828  Application      User_52   
4  statechange    ApplState_946455804  Application      User_52   

           concept:name lifecycle:transition   
0  A_Create Application             complete  \
1           A_Submitted             complete   
2             A_Concept             complete   
3            A_Accepted             complete   
4            A_Complete             complete   

                     time:timestamp           case:LoanGoal   
0  2016-01-01 10:51:15.304000+01:00  Existing loan takeover  \
1  2016-01-01 10:51:15.352000+01:00  Existing loan takeover   
2  2016-01-01 10:52:36.413000+01:00  Existing loan takeover   
3  2016-01-02 12:23:04.299000+01:00  Existing loan takeover   
4  2016-01-02 12:30:28.633000+01:00  Existing loan takeover   

       case:concept:name  case:RequestedAmount case:ApplicationType  
0  Application_652823628               20000.0           New credit  
1  Application_652823628               20000.0           New credit  
2  Application_652823628               20000.0           New credit  
3  Application_652823628               20000.0           New credit  
4  Application_652823628               20000.0           New credit

In [7]:
from pm4py.objects.log.util.log import project_traces
def print_nth(log, index):
    print(str(project_traces(event_log)[index]))

In [8]:
print_nth(event_log, 0)

['A_Create Application', 'A_Submitted', 'A_Concept', 'A_Accepted', 'A_Complete', 'A_Validating', 'A_Incomplete', 'A_Validating', 'A_Pending']


In [9]:
print_nth(event_log, 1)

['A_Create Application', 'A_Submitted', 'A_Concept', 'A_Accepted', 'A_Complete', 'A_Cancelled']


In [10]:
dfg, start_activities, end_activities = pm4py.discover_dfg(event_log)
pm4py.view_dfg(dfg, start_activities, end_activities)

ExecutableNotFound: failed to execute PosixPath('dot'), make sure the Graphviz executables are on your systems' PATH

In [11]:
# alpha miner - net (places and transactions)
# general way to visualize net or tree or graph in pm4py - pm4py.view_{petri_net/tree/...}
net, initial_marking, final_marking = pm4py.discover_petri_net_alpha(event_log)
pm4py.view_petri_net(net)

ExecutableNotFound: failed to execute PosixPath('dot'), make sure the Graphviz executables are on your systems' PATH

In [12]:
# inductive miner algoritham, we can plot perocess tree, and can save the net same as alpha miner ((places and transactions))
net, initial_marking, final_marking = pm4py.discover_petri_net_inductive(event_log)
tree = pm4py.discover_process_tree_inductive(event_log)
pm4py.view_process_tree(tree)

ExecutableNotFound: failed to execute PosixPath('dot'), make sure the Graphviz executables are on your systems' PATH

In [13]:
# huristic miner
heu_net = pm4py.discover_heuristics_net(event_log, dependency_threshold=0.99)
pm4py.view_heuristics_net(heu_net)

InvocationException: GraphViz's executables not found

In [14]:
# check type and correct if needed
df.dtypes

Action                   object
EventID                  object
EventOrigin              object
org:resource             object
concept:name             object
lifecycle:transition     object
time:timestamp           object
case:LoanGoal            object
case:concept:name        object
case:RequestedAmount    float64
case:ApplicationType     object
dtype: object

In [15]:
df['time:timestamp'] = pd.to_datetime(df['time:timestamp'], utc=True)
df['Year'] = df['time:timestamp'].dt.year
df['Month'] = df['time:timestamp'].dt.month

In [16]:
df.head(5)

Action                EventID  EventOrigin org:resource   
0      Created  Application_652823628  Application       User_1  \
1  statechange   ApplState_1582051990  Application       User_1   
2  statechange    ApplState_642383566  Application       User_1   
3  statechange     ApplState_99568828  Application      User_52   
4  statechange    ApplState_946455804  Application      User_52   

           concept:name lifecycle:transition                   time:timestamp   
0  A_Create Application             complete 2016-01-01 09:51:15.304000+00:00  \
1           A_Submitted             complete 2016-01-01 09:51:15.352000+00:00   
2             A_Concept             complete 2016-01-01 09:52:36.413000+00:00   
3            A_Accepted             complete 2016-01-02 11:23:04.299000+00:00   
4            A_Complete             complete 2016-01-02 11:30:28.633000+00:00   

            case:LoanGoal      case:concept:name  case:RequestedAmount   
0  Existing loan takeover  Application_652823628               20000.0  \
1  Existing loan takeover  Application_652823628               20000.0   
2  Existing loan takeover  Application_652823628               20000.0   
3  Existing loan takeover  Application_652823628               20000.0   
4  Existing loan takeover  Application_652823628               20000.0   

  case:ApplicationType  Year  Month  
0           New credit  2016      1  
1           New credit  2016      1  
2           New credit  2016      1  
3           New credit  2016      1  
4           New credit  2016      1

In [17]:
# Separate trace and event attributes
trace_attr = []
event_attr = []

for name, group in df.groupby(['case:concept:name']):
    trace_attributes = []
    event_attributes = []

    for col in group.columns:
        if len(set(group[col])) == 1:
            trace_attributes.append(col)
        else:
            event_attributes.append(col)

    trace_attr.append({'case:concept:name': name, 'trace_attributes': trace_attributes})
    event_attr.append({'case:concept:name': name, 'event_attributes': event_attributes})

# Display the results
print("Trace Attributes:")
for item in trace_attr:
    print(item)

print("\nEvent Attributes:")
for item in event_attr:
    print(item)

Trace Attributes:
{'case:concept:name': ('Application_1000158214',), 'trace_attributes': ['EventOrigin', 'lifecycle:transition', 'case:LoanGoal', 'case:concept:name', 'case:RequestedAmount', 'case:ApplicationType', 'Year', 'Month']}
{'case:concept:name': ('Application_1000334415',), 'trace_attributes': ['EventOrigin', 'lifecycle:transition', 'case:LoanGoal', 'case:concept:name', 'case:RequestedAmount', 'case:ApplicationType', 'Year', 'Month']}
{'case:concept:name': ('Application_100034150',), 'trace_attributes': ['EventOrigin', 'lifecycle:transition', 'case:LoanGoal', 'case:concept:name', 'case:RequestedAmount', 'case:ApplicationType', 'Year']}
{'case:concept:name': ('Application_1000386745',), 'trace_attributes': ['EventOrigin', 'lifecycle:transition', 'case:LoanGoal', 'case:concept:name', 'case:RequestedAmount', 'case:ApplicationType', 'Year']}
{'case:concept:name': ('Application_1000474975',), 'trace_attributes': ['EventOrigin', 'lifecycle:transition', 'case:LoanGoal', 'case:concept